In [93]:
import re
from bs4 import BeautifulSoup
import requests
import html5lib
import json

In [94]:
url = 'https://www.cna.com.tw/list/aspt.aspx'
res = requests.get(url)
soup = BeautifulSoup(res.text,'html5lib')

In [95]:
n=0
labels=[]
#label_dic = {}
while n < len(soup.select_one('#pnProductNavContents > ul').findAll('li')):
    try :
        lab = soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'}).text
        url =soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'})['href']
    except:(TypeError,IndentationError)
    labels.append((url,lab))
    n += 1
labels = list(set(labels))
labels.remove(('http://cnavideo.cna.com.tw', '影音'))
labels.remove(('/list/aall.aspx', '即時'))
labels.append(('https://www.cna.com.tw/list/aall.aspx', '即時'))
#labels.remove(('https://www.cna.com.tw/keyword/九合一.aspx', '九合一'))
labels.remove(('https://www.cna.com.tw/list/sp.aspx', '專題'))
labels.remove(('https://www.cna.com.tw/list/aall.aspx', '即時'))

In [96]:
labs = []
for item in labels:
    item = [item[0],item[1]]

    item[0] = re.search(r'list\/\w+',item[0]).group()[5:]
    labs.append(item)

In [97]:
def payload(item):
    payload={
        'id': '1056893641102242',
    'ev': 'Microdata',
    'dl': item[0],
    'rl': 'https://www.cna.com.tw/',
    'if': 'false',
    'ts': '1541087113735',
    'cd[Schema.org]': [],
    #'cd[OpenGraph]': {"og:url":"https://www.cna.com.tw/list/ahel.aspx","og:title":"生活 | 中央社 CNA","og:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","og:image:height":"200","og:image:width":"200","og:image":"https://img5.cna.com.tw/www/images/pic_fb.jpg","og:type":"article","article:author":"https://www.facebook.com/cnanewstaiwan","article:publisher":"https://www.facebook.com/cnanewstaiwan"}
    #'cd[Meta]': {"title":"\n\t生活 | 中央社 CNA\n","meta:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","meta:keywords":"News, 新聞, 即時新聞, 中央社"}
    'cd[DataLayer]': [],
    'cd[JSON-LD]': [],
    'sw': '1280',
    'sh': '5000',#'720',
    'v': '2.8.30',
    'r': 'stable',
    'a': 'tmgoogletagmanager',
    'ec': '1',
    'o': '30',
    'fbp': 'fb.2.1541074934894.620990608',
    'it': '1541087112886',
    'coo': 'false',
    'es': 'automatic',
    }
    return payload

In [98]:
labs_soup=[]
for item in labs:
    soups=[]
    n=1
    while n < 13:
        url = 'https://www.cna.com.tw/cna2018api/api/simplelist/categorycode/'+item[0]+'/pageidx/'+str(n)
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        body = soup.findAll('body')[0].getText()
        PageUrl = re.findall(r'\"PageUrl\"\:\S[^\,]+',body)
        urls = [txt[11:-1] for txt in PageUrl]
        soups.extend(urls)
        n += 1
        if len(urls) < 20:
            break
    labs_soup.append([soups,item[1]])

In [99]:
news={}
newslist=[]
for lab in labs_soup:
    lab_name = lab[1]
    lab_urls = lab[0]
    n = 0
    for url in lab_urls:
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        txt = ""
        try:
            title = soup.find_all('div',{'class':'centralContent'})[0].find_all('h1')[0].getText()
            for s in soup.find_all('div',{'class':'paragraph'})[0].findAll('p'):
                txt=txt+s.getText()
        except:IndexError
        research = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt)
        if research == None or len(research.group())<2:
            print(txt)
        else:
            txt = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt).group()[1:]

        page = [[title,txt],lab_name]
        newslist.append(page)
        news[txt]=lab_name
        n += 1
        if n % 20 == 0:
            print((lab_name,n),end=",")


('科技', 20),('科技', 40),('科技', 60),('科技', 80),('科技', 100),('地方', 20),('地方', 40),('地方', 60),('地方', 80),('地方', 100),('社會', 20),('社會', 40),('社會', 60),('社會', 80),('社會', 100),('運動', 20),('運動', 40),('運動', 60),('運動', 80),('運動', 100),('兩岸', 20),('兩岸', 40),中央社駐香港特派員張謙/12月3日4年前「占中運動」爆發時，香港泛民主派一度氣勢如虹，並於2016年底的立法會選舉取得不錯成績，但近年來形勢逆轉，泛民面對不少內憂壓力。挾著年輕力量的崛起，泛民於2016年9月的立法會選舉大有斬獲，共取得26席。當中包括一人一票的分區直選議席，以及以業界區分的功能組別議席。功能組別以業界人士或代表區分，從來都是泛民較弱的版塊，但當年泛民在這方面獲得的選票大增，顯示其勢力正往業界延伸，威脅親政府建制派的基本盤。但「占中」之後，當局在北京中央高喊必須對「港獨」零容忍的情況下，開始以行政手段限制立場較為偏激的泛民人士參選。主要要求各候選人在參選前，必須簽署一份參選聲明，表明自己擁護基本法和保證效忠香港特別行政區。這項新規定導致一些泛民代表、特別是主張「港獨」的年輕代表，無法參加當年的立法會選舉，甚至讓新成立的年輕政黨香港眾志，一夜之間被排除在選舉之外，無法透過參選而進入香港管治架構。選後，當局也對泛民當選者窮追猛打，以他們在宣誓就任時未符合基本法所規定的「莊嚴」要求，向法院提出聲請，要求褫奪他們的資格，結果導致泛民6人喪失議席。進入2018年，泛民的困境並未消除。在立法會議員補選中未能拿回失去的全部議席，僅取回3席，失去另外2席，讓泛民在議會的人數減少。今年3月和11月，當局為泛民失去的其中5個議席進行補選，其中3月補選4人，11月補選1人。結果泛民在3月只贏回兩席，失去另外2席。更重要的是，泛民在一人一票的地方直選，被建制派打敗而失去1席，這是泛民和建制派歷來在一對一的對決下，首次落敗。在上月的補選中，泛民同樣在地方直選中落敗，受挫的的更是泛民元老級人馬、工黨成員李卓人。對於泛民連續兩次在一人一票地方直選、一對一對決之下敗給建制派，有學者解讀為泛民和建制的

In [100]:
newslist[1]

[['Google推出隨選語音新聞 透過人工助理就能播放',
  '谷歌（Google）今天表示，將推出類似廣播的隨選語音新聞服務，能透過智慧喇叭收聽，並藉助人工智慧加以個人化。谷歌表示，已與十多個新聞組織合作，來發送語音新聞，作法與智慧手機上的新聞源相同。谷歌產品經理蓋納斯（Liz Gannes）在部落格上說：「這種新聞體驗會帶給你即時收集的語音新聞播放清單，為你量身打造。」「一開始播送的是頭條新聞和新聞更新提示，接著播送比較長的詳細內容。」谷歌開發的人工智慧程式「谷歌助理」會處理內容，使用者可跳過、倒轉或暫停新聞。這項計畫力求將語音新聞轉型成隨選影片供應商網飛（Netflix）式的服務，並能夠依據個人化建議隨機選擇新聞。這項計畫透過谷歌喇叭和智慧手機播送，使谷歌現有的新聞傳播業務更上層樓。此時各新聞機構和科技公司正普遍努力開發更多語音服務。'],
 '科技']

In [101]:
import jieba
import nltk

In [102]:
stopwords=[]
with open('stopwords_ch.txt', 'r', encoding='UTF-8') as file:
    for data in file.readlines():
        data = data.strip()
        stopwords.append(data)

In [103]:
filterwords=[
    '年','月','中央社','記者','編輯','譯者','日電',
    '\n',' ','「','」'
    ,'今天','說','表示','年','月','日','後','前','時','應','中','今年'
    ,'兩','下','人','最','次','再','先','盡量'
]

In [104]:
articles = []
titles = []
for news in newslist:
    articles.append((news[0][1],news[1]))
    titles.append((news[0][0],news[1]))


In [105]:
books = []

n = 0
while n < len(titles):
    head_dic = {}
    txt_dic = {}
    head = titles[n]
    txt = articles[n]
    
    head_dic[head[0]] = head[1]
    txt_dic[txt[0]] = txt[1]
    books.append([head_dic,txt_dic])
    n += 1

In [106]:
# book = [ head_dic , txt_dic ]
books[1]

[{'Google推出隨選語音新聞 透過人工助理就能播放': '科技'},
 {'谷歌（Google）今天表示，將推出類似廣播的隨選語音新聞服務，能透過智慧喇叭收聽，並藉助人工智慧加以個人化。谷歌表示，已與十多個新聞組織合作，來發送語音新聞，作法與智慧手機上的新聞源相同。谷歌產品經理蓋納斯（Liz Gannes）在部落格上說：「這種新聞體驗會帶給你即時收集的語音新聞播放清單，為你量身打造。」「一開始播送的是頭條新聞和新聞更新提示，接著播送比較長的詳細內容。」谷歌開發的人工智慧程式「谷歌助理」會處理內容，使用者可跳過、倒轉或暫停新聞。這項計畫力求將語音新聞轉型成隨選影片供應商網飛（Netflix）式的服務，並能夠依據個人化建議隨機選擇新聞。這項計畫透過谷歌喇叭和智慧手機播送，使谷歌現有的新聞傳播業務更上層樓。此時各新聞機構和科技公司正普遍努力開發更多語音服務。': '科技'}]

In [107]:
def get_tags(books=books):

    prelab = ''
    tags = {}
    for book in books:
        head_dic = book[0]
        txt_dic = book[1]
        n=0
        for dic in [head_dic,txt_dic]:

            for lab in ['生活','運動','政治','科技','國際','兩岸','產經','社會','地方','娛樂','證券','文化']:
                if list(dic.values())[0]==lab:
                    if prelab != lab:
                        txt=''
                    txt += list(dic.keys())[0]
                    tags[list(dic.values())[0]] = txt
                    prelab = lab
            if n == 0:
                title_tags = tags
            elif n == 1:
                txt_tags = tags
            n += 1
    return title_tags,txt_tags

In [108]:
title_tags,txt_tags = get_tags(books)

In [109]:
title_tags

{'兩岸': '美藉貿易戰促結構改革  陸學者：需具備4條件美國總統川普藉由貿易戰的手段，促使北京在經濟上進行結構性改革，但是大陸學者今天強調，「中國的改革不是哪個人可決定的」，改革需具備條件、成本、代價和時機等4項條件。中國社會科學院政治學研究所所長房寧今天在中國記協茶話會以「改革開放40年：中國政治改革與發展」為題，和中外媒體交流。外媒關切，中方是否將做出改革，或是與美國陷入冷戰。房寧表示，中國大陸經濟發展處於重要階段，有機會轉型升級更上一層樓，但也可能會有很多矛盾，例如陷入中等收入陷阱，或如同日本在90年代初出現泡沫經濟，造成往後失落的10年、甚至20年。他說，「中國經濟目前的嚴峻處境並非危言聳聽」；中國在這個階段與美國發生貿易戰，情況讓人非常擔憂。對於川普希望中國大陸經濟進行改革一事，房寧表示能夠理解，畢竟中美都是世界重要的經濟體，但是川普提出的要求標準很高，由於問題不是一兩天形成的，「要在短時間內扭轉過來並不現實」。房寧坦言，中國政府知道必須進行改革以解決問題，「但是中國的改革不是哪個人決定的，不是中國的政府、執政黨可以任意制定政策，進行改革」。他表示，改革要從實際出發，有條件、成本、代價和時機。只有這4個條件都具備了，在主觀的努力下，改革才更容易推進。選後兩岸交流變化  張小月：和海基會工作不衝突九合一選舉國民黨贏得15縣市，未來兩岸城市經貿交流可能升溫。對於海基會是否會扮演積極角色，海基會董事長張小月說，促進兩岸經貿本來就是海基會一直在推動的工作。海峽交流基金會今天舉行第十屆董監事第五次聯席會議，據與會人員轉述，海基會董事、國民黨大陸事務部主任周繼祥在臨時動議中提出，國民黨在這次地方選舉拿下的縣市正摩拳擦掌要推動兩岸經貿，讓「貨出去、人進來」，海基會應該在其中扮演積極的角色。據轉述，張小月及海基會副董事長姚人多都回應，促進兩岸經貿和兩岸人民的往來，一向就是海基會在推動的工作，沒有衝突。今天的會議也通過補選第10屆部分董監事案。因應教育部常務次長林騰蛟、法務部前政務次長蔡碧仲業務調整和職務異動等原因，由派任機關函告免兼海基會董事職務並改推薦新任接替人選。前花蓮縣長傅崑萁9月判刑定讞被解職後，蔡碧仲被行政院指派為花蓮縣代理縣長。經過補選程序後，通過由教育部政務次長姚立德補任第10屆董事，法務部常務次長張斗輝補任第10屆監事。中國5G試驗頻段確定 2020年

In [110]:
txt_tags

{'兩岸': '美藉貿易戰促結構改革  陸學者：需具備4條件美國總統川普藉由貿易戰的手段，促使北京在經濟上進行結構性改革，但是大陸學者今天強調，「中國的改革不是哪個人可決定的」，改革需具備條件、成本、代價和時機等4項條件。中國社會科學院政治學研究所所長房寧今天在中國記協茶話會以「改革開放40年：中國政治改革與發展」為題，和中外媒體交流。外媒關切，中方是否將做出改革，或是與美國陷入冷戰。房寧表示，中國大陸經濟發展處於重要階段，有機會轉型升級更上一層樓，但也可能會有很多矛盾，例如陷入中等收入陷阱，或如同日本在90年代初出現泡沫經濟，造成往後失落的10年、甚至20年。他說，「中國經濟目前的嚴峻處境並非危言聳聽」；中國在這個階段與美國發生貿易戰，情況讓人非常擔憂。對於川普希望中國大陸經濟進行改革一事，房寧表示能夠理解，畢竟中美都是世界重要的經濟體，但是川普提出的要求標準很高，由於問題不是一兩天形成的，「要在短時間內扭轉過來並不現實」。房寧坦言，中國政府知道必須進行改革以解決問題，「但是中國的改革不是哪個人決定的，不是中國的政府、執政黨可以任意制定政策，進行改革」。他表示，改革要從實際出發，有條件、成本、代價和時機。只有這4個條件都具備了，在主觀的努力下，改革才更容易推進。選後兩岸交流變化  張小月：和海基會工作不衝突九合一選舉國民黨贏得15縣市，未來兩岸城市經貿交流可能升溫。對於海基會是否會扮演積極角色，海基會董事長張小月說，促進兩岸經貿本來就是海基會一直在推動的工作。海峽交流基金會今天舉行第十屆董監事第五次聯席會議，據與會人員轉述，海基會董事、國民黨大陸事務部主任周繼祥在臨時動議中提出，國民黨在這次地方選舉拿下的縣市正摩拳擦掌要推動兩岸經貿，讓「貨出去、人進來」，海基會應該在其中扮演積極的角色。據轉述，張小月及海基會副董事長姚人多都回應，促進兩岸經貿和兩岸人民的往來，一向就是海基會在推動的工作，沒有衝突。今天的會議也通過補選第10屆部分董監事案。因應教育部常務次長林騰蛟、法務部前政務次長蔡碧仲業務調整和職務異動等原因，由派任機關函告免兼海基會董事職務並改推薦新任接替人選。前花蓮縣長傅崑萁9月判刑定讞被解職後，蔡碧仲被行政院指派為花蓮縣代理縣長。經過補選程序後，通過由教育部政務次長姚立德補任第10屆董事，法務部常務次長張斗輝補任第10屆監事。中國5G試驗頻段確定 2020年

In [1346]:
def get_fwords(tags={},top=300):


    lab_fwords={}
    lab_Ftwowords = {}
    for labname in tags.keys():
        print(labname,end=',')
        lab_words = tags[labname]
    #    seg_list = jieba.cut_for_search(lab_words)#, cut_all=False)
        seg_list = jieba.cut(lab_words, cut_all=False)
        txt = ",".join(seg_list)
        tokens = txt.split(',')
        tokens = list(filter(lambda a: a not in stopwords and a not in filterwords and a.isalpha() == True,tokens))#and len(a)>1, tokens))
        ###
        lab_alltwowords = list(nltk.bigrams(tokens))
        two = nltk.FreqDist(lab_alltwowords).most_common(top)
        lab_Ftwowords[labname] = [i[0]+i[1] for i,j in two]
        ###
        lab_fwords[labname] =  [i[0] for i in nltk.FreqDist(tokens).most_common(top)]
    return lab_fwords,lab_Ftwowords

In [1347]:
txt_fwords,txt_Ftwowords = get_fwords(txt_tags)

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [2632]:
txt_fwords2 = get_fwords(txt_tags)[0]

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [1348]:
title_fwords['國際']

['美國',
 '華為',
 '中國',
 '政府',
 '孟晚',
 '舟',
 '加拿大',
 '已',
 '報導',
 '日本',
 '公司',
 '川普',
 '國家',
 '英國',
 '台灣',
 '關係',
 '被捕',
 '總統',
 '協議',
 '北韓',
 '要求',
 '名',
 '全球',
 '網路',
 '企業',
 '逮捕',
 '進行',
 '指出',
 '調查',
 '設備',
 '制裁',
 '認為',
 '南韓',
 '違反',
 '支持',
 '曾',
 '媒體',
 '國會',
 '脫歐',
 '通訊',
 '是否',
 '貿易',
 '民眾',
 '安全',
 '項',
 '新',
 '問題',
 '發展',
 '引渡',
 '非',
 '伊朗',
 '行動',
 '遭',
 '財務長',
 '工作',
 '當局',
 '官員',
 '相關',
 '技術',
 '科技',
 '梅伊',
 '歲',
 '目前',
 '中興',
 '國際',
 '禁止',
 '約',
 '美',
 '任正',
 '提出',
 '臉書',
 '人士',
 '黃',
 '背心',
 '消息',
 '措施',
 '印度',
 'PEI',
 '土耳其',
 '主要',
 '抗議',
 '梅克爾',
 '活動',
 '北京',
 '布希',
 '元',
 '機構',
 '政治',
 '重要',
 '聯邦',
 '人員',
 '採購',
 '計畫',
 '事件',
 '法院',
 '反對',
 '電信',
 '會議',
 '決定',
 '手機',
 '代表',
 '透過',
 '創辦人',
 '歐洲',
 '希望',
 '包括',
 '舉行',
 '澳洲',
 '做',
 '南北韓',
 '成為',
 '溝通',
 '情報',
 '市場',
 '使用',
 '些',
 '中方',
 '針對',
 '未來',
 '投票',
 '總理',
 '組織',
 '一直',
 '家',
 '駐',
 '美方',
 '談話',
 '法律',
 '訪問',
 '以來',
 '華府',
 '這是',
 '加入',
 '影響',
 '無',
 '大學',
 '許多',
 '美軍',
 '引述',
 '顯示',
 '政策',
 '歐盟',
 '產品',
 '提供',
 '進

In [1349]:
#type(get_fwords(title_tags))

In [1350]:
#去除交集的高頻字
def remove_mix(t):
    lab_fwords = t[0]
    lab_Ftwowords = t[1]


    dic3={}
    for lab in lab_fwords.keys():   
        word_content2 = lab_fwords[lab].copy()
        for lab2 in lab_fwords.keys():        
            if lab != lab2:
                word_content = [w for w in lab_fwords[lab] if (w in [a for a in lab_fwords[lab2]])]
                for w in word_content:
                    try:
                        word_content2.remove(w)                  
                    except ValueError:
                        pass
        dic3[lab] = word_content2  



    dic2={}
    for lab in lab_Ftwowords.keys():   
        word_content2 = lab_Ftwowords[lab].copy()
        for lab2 in lab_Ftwowords.keys():        
            if lab != lab2:
                word_content = [w for w in lab_Ftwowords[lab] if (w in [a for a in lab_Ftwowords[lab2]])]
                for w in word_content:
                    try:
                        word_content2.remove(w)                   
                    except ValueError:
                        pass
        dic2[lab] = word_content2
        
    return dic3,dic2

In [2482]:
title_fwords,title_Ftwowords = remove_mix(get_fwords(title_tags,700))
txt_fwords,txt_Ftwowords = remove_mix(get_fwords(txt_tags,800))

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [2483]:
'陳菊' in txt_fwords['文化']

False

In [2484]:
[i for i in txt_fwords['政治'] if i in txt_fwords['文化']]

[]

In [2485]:
def get_allFtwowords(lab_Ftwowords={}):
    
    
    All_Ftwowords2=[]
    for n in lab_Ftwowords.values():
        for m in n:
            All_Ftwowords2.append(m)

    All_Ftwowords = []
    for w in All_Ftwowords2:
        All_Ftwowords.append(w)
    return All_Ftwowords

In [2486]:
title_allFtwo = get_allFtwowords(title_Ftwowords)
txt_allFtwo = get_allFtwowords(txt_Ftwowords)

In [2487]:
txt_allFtwo

['太空總署',
 '報導蘋果',
 '國家航空',
 '航空暨',
 '暨太空',
 '總署NASA',
 '無線通訊',
 '身分識別',
 '研究團隊',
 'AppleWatch',
 '國外科技',
 '科技網站',
 '運載火箭',
 '國際太空站',
 '發射升空',
 '邱培鈺',
 '加密貨幣',
 '用戶資料',
 '先前報導',
 '漢諾威電腦展',
 '登陸火星',
 '火星探測',
 'Google翻譯',
 '臉部辨識',
 '熱門話題',
 '逐字稿',
 '螢幕指紋',
 '聯合號火箭',
 '太空葬',
 '溫室氣體',
 '離子風',
 'GSLVMk',
 'MkIII',
 '版iPhone',
 '小行星',
 'TWID身分',
 '萬公里',
 '降落火星',
 '台法科技獎',
 '董明珠',
 '探測任務',
 '電子郵件',
 '臉書Facebook',
 '加拉巴戈',
 '巴戈斯',
 '樂土太空',
 '歐塞瑞斯',
 '法國國家',
 '蘋果深耕',
 '外媒先前',
 '識別服務',
 '航太總署',
 '噴射推進',
 '推進實驗室',
 '微創手術',
 '蘋果積極',
 '通訊晶片',
 '成功發射',
 '雅婷逐字',
 '美國太空',
 '送入太空',
 '軌道衛星',
 '網站Patently',
 'PatentlyApple',
 '俄羅斯聯合號',
 '瑞斯號',
 '科學研究',
 '翻譯網頁',
 '光達技術',
 '太空軌道',
 '指出蘋果',
 '發射羅老',
 '羅老號',
 '識別中心',
 '成果發表',
 '海達路德',
 '探測器洞察號',
 '火星表面',
 '洞察號InSight',
 '火星探測器',
 '火星地震',
 '比特幣價格',
 '火星大氣層',
 '訓練中心',
 '電子元件',
 '北斗三號',
 '發射任務',
 '晶片設計',
 'AI領域',
 '超級電腦',
 '台灣杉二號',
 '語音新聞',
 '無法使用',
 '透過手機',
 '顯示臉書',
 '重要里程碑',
 '重達公斤',
 '年度熱門',
 '行動裝置',
 '柯諾',
 '諾年科',
 '格林威治時間',
 '火箭發射',
 '新創公司',
 '微型衛星',
 '情色內容

In [2488]:
import random
random.shuffle(books)

In [2489]:
def pos_title_features(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in title_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top*2/3))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))
    if len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0:
        for i in ftwowords:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
        for i in ftwowords:
            w = i[0]
            if w in [w for li in title_Ftwowords.values() for w in li]:
                features[w] = True
#                print(w+'2')

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    if len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0:
        for i in toks:
            #features[i] = True
            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in title_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in title_fwords[k] :

##                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k
##            print(len(bigcontent))
        for tok in bigcontent:  
#                print(tok+','+kk)
            features[tok] = True
    #                print(tok+'4')
    #        print(tok+'1')
    return features

In [2490]:
pos_title_features(test_title,200)

民眾3
提點3
點子3
提點子3
成案3
公投3
剝奪3
基本權3


{}

In [2765]:
def get_title_featuresets(book,top=200):
    n = 0
    featuresets=[]
#    for book in books:
    head_dic = book[0]
#        features = {}
    article = list(head_dic.keys())[0]
    labname = list(head_dic.values())[0]
    features = pos_title_features(article,top)

    if len(list(features.keys())) < 2:
        #feature_item = [features,labname]
        pass
    else:
        feature_item = [features,labname]
        featuresets.append(feature_item)
    n += 1
    if n % 20 == 0:
        print(n,end=',')

    return featuresets
#    return feature_item

In [2766]:
def pos_txt_features0(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top*2/3))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0:
        for i in ftwowords:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
        for i in ftwowords:
            w = i[0]
            if w in [w for li in txt_Ftwowords.values() for w in li]:
                features[w] = True
#                print(w+'2')

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
            print(i+'3')
    else:
        for tok in toks:
            if tok in [w for li in txt_fwords.values() for w in li]:
                features[tok] = True
#                print(tok+'4')
#        print(tok+'1')
    return features

In [2767]:
def pos_txt_features(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))

    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
#            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in txt_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in txt_fwords[k] :

                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k

##           print(len(bigcontent))
        for tok in bigcontent:  
            print(tok+','+kk)
            features[tok] = True
    #                print(tok+'4')
    #        print(tok+'1')
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0:
        for i in ftwowords[:int(len(ftwowords)*0.25)]:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk2=''
        for k in txt_Ftwowords.keys():
            content=[]
            for i in ftwowords:
                tok = i[0]
    #                print([w for li in txt_Ftwowords[k] for w in li])
                if tok in txt_Ftwowords[kk] :

                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
#                    kk = k
##            print(len(bigcontent))
            for tok in bigcontent:  
#                print(tok+','+kk)
                features[tok] = True

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    return features

In [2768]:
def get_txt_Flab0(article,top,get=5):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))

    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
#            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in txt_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in txt_fwords[k] :

 #                   print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k
##           print(len(bigcontent))
        for tok in bigcontent[:get]:  
##                print(tok+','+kk)
            features[tok] = kk
            print(tok+'4')
    #        print(tok+'1')
    
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0:
        print(4)
        for i in ftwowords[:int(len(ftwowords)*0.25)]:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
#        for tok in toks:
        print('3')
        bigcontent2=[]
        kk2=''
        for k in txt_Ftwowords.keys():
            content2=[]
            for i in ftwowords:
                tok = i[0]
    #                print([w for li in txt_Ftwowords[k] for w in li])
                if tok in txt_Ftwowords[kk] :

#                    print(tok+'1'+k)
                    content2.append(tok)
                if len(bigcontent2) < len(content2):
                    bigcontent2 = content2.copy()
                    kk2 = kk
##            print(len(bigcontent))
            for tok in bigcontent2[:get]:  
 #               print(tok+'3'+kk2)
                features[tok] = kk2

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    return features

In [2769]:
from collections import Counter
def get_top(article,top,get=5):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(toks)
    selectwords = ([t for t in toks if t[0] in [w for li in txt_fwords.values() for w in li]])
    klist=[]
    for w in selectwords[:get]:
       
        for k in txt_fwords.keys():

            if w[0] in [s for s in txt_fwords[k]] :
                klist.append(k)
                print(w,k)
                features['top'] = Counter(klist).most_common(1)[0][0]



    return features

In [2770]:
get_top(test_txt,200,5)

('塞爾', 6) 運動
('連勝', 4) 運動
('全場', 3) 運動
('主場', 2) 運動
('替補', 2) 運動


{'top': '運動'}

In [2771]:
[s for li in txt_fwords.values() for s in li]

['火星',
 '太空',
 '火箭',
 '發射',
 '洞察號',
 '地球',
 '用戶',
 'NASA',
 '總署',
 '軌道',
 '降落',
 '升空',
 'Facebook',
 '科學家',
 '科技部',
 '太空人',
 '裝置',
 '探測器',
 'Apple',
 '識別',
 '登陸',
 '外媒',
 '探測',
 'Google',
 '無線',
 '螢幕',
 '機器人',
 '比特幣',
 '氣味',
 '人類',
 '太空船',
 '行星',
 '好奇號',
 '軟體',
 '軟銀',
 '氣體',
 '月球',
 '實驗室',
 '太空站',
 '貨幣',
 '搭載',
 '當機',
 'ISRO',
 '基因',
 'Instagram',
 '速度',
 '象龜',
 '大小',
 '陳良基',
 'Oath',
 '運載',
 '谷歌',
 '運算',
 '漢諾威',
 '台法',
 '離子',
 'Watch',
 '語音',
 '失敗',
 '追蹤',
 '諾',
 '組成',
 '聯合號',
 '加州',
 '太陽系',
 '加密',
 '電腦展',
 '引擎',
 '版',
 '資訊月',
 '巴西',
 '材料',
 '英特爾',
 '星',
 '葬',
 '骨灰',
 '大氣層',
 '貝努',
 '光達',
 '表面',
 '氣候',
 '動力',
 '培鈺',
 '莫內',
 '用來',
 'SpaceX',
 '祖克柏',
 'Telstra',
 '重',
 'Space',
 '試射',
 '網頁',
 '研究院',
 '名為',
 '虛擬',
 '郵輪',
 '明珠',
 'Fitbit',
 '珊瑚',
 '三號',
 '臉部',
 '愛立信',
 '故障',
 '逐字',
 '稿',
 '通信',
 '發動機',
 '馬斯克',
 '商業化',
 'GSAT',
 'Tumblr',
 '瑞斯',
 '樣本',
 '化學',
 '專利',
 '效能',
 'InSight',
 '溫室',
 '風',
 '董',
 '闖紅燈',
 'GSLV',
 'Mk',
 'III',
 'Dialog',
 'LCP',
 '用於',
 '雅婷',
 '帳號',
 '大廠',
 '預定',
 

In [2772]:
txt_fwords.keys()

dict_keys(['科技', '地方', '社會', '運動', '兩岸', '證券', '生活', '娛樂', '國際', '產經', '政治', '文化'])

In [2773]:
def get_txt_featuresets(book,top=200):
    n = 0
    featuresets=[]
#    for book in books:
    txt_dic = book[1]
#        features = {}
    article = list(txt_dic.keys())[0]
    labname = list(txt_dic.values())[0]
    features = pos_txt_features(article,top)
    feature_item = [features,labname]
    featuresets.append(feature_item)
    n += 1
    if n % 20 == 0:
        print(n,end=',')

#    return featuresets
    return feature_item

In [2774]:
test_title="""
NBA／厄文爆發布朗覺醒 綠衫軍主場大勝尼克取4連勝

"""

test_txt="""
取得3連勝的波士頓塞爾提克今(7)日在主場迎戰紐約尼克，靠著「Uncle Drew」Kyrie Irving(厄文)在第3節大爆發、全場砍下22分，以及Jaylen Brown(布朗)「復活」以替補身分得到21分，塞爾提克終場以128:100擊敗對手，喜迎4連勝。

 

在開季不穩的狀況之後，綠衫軍近期慢慢步上正軌，連勝鵜鶘、騎士、灰狼3支隊伍，目前處於3連勝的高昂士氣當中。今天面對近年的弱隊尼克，他們當然渴望能再拿下一場勝利。

 

Gordon Hayward和Brown本季的狀況都不算太好，似乎還在和球隊磨合當中，不過今天首節他們兩人表現出色，賽爾提克也因此拿到了38分的高分。次節塞隊替補後衛Terry Rozier連續砍進兩顆三分球，幫助球隊領先到達9分，終場前30.1秒中鋒Al Horford上籃得手，塞爾提克以69:58進入到下半場。

 

第3節比賽進入到Irving的表演時間，他單節轟下14分，包括了3記重要的三分彈，塞爾提克也在該節結束後將分差拉開到15分。末節尼克無心再戰，塞爾提克也對比賽有了一些想法，雙方陸續開始走馬換將，比賽結果也大致底定，最終主場軍以28分之差贏球。

 

塞爾提克今天全隊命中率高達53.3%，反觀尼克只有40.9%，成為雙方勝負的分野。Irving此役攻下全場最高的22分，另外還有8次助攻，表現非常全面。而從板凳出發的Brown，則是打出讓人激賞的高效率，全場出賽24分鐘，10投7中得到21分。

 

尼克方面，Tim Hardaway Jr.也得到了22分，但19投僅7中，命中率並不理想。Emmanuel Mudiay則是拿到了17分和6次的助攻。

"""

In [2775]:
pos_title_features(test_title,15)

{'NBA': True, '主場': True, '連勝': True}

In [2776]:
get_title_featuresets(books[0],top=200)

[[{'夫妻': True, '奈奈': True, '奈奈夫妻': True, '涉詐欺': True, '詐欺': True, '貴婦': True},
  '社會']]

In [2777]:
books[0]

[{'貴婦奈奈夫妻涉詐欺 挨告前飛往舊金山[更新]': '社會'},
 {'網紅貴婦奈奈和先生黃博健合開的「杏立博全」醫美診所無預警歇業，3日遭人控告他們涉詐欺；但檢警獲報，這對夫婦在11月30日持中華民國護照搭機飛往美國舊金山。台北地檢署調查，貴婦奈奈和她的先生10月28日持中華民國護照出境前往日本，當天就持中華民國護照返台；11月30日，貴婦奈奈和她的先生持中華民國護照出境飛往美國舊金山。「杏立博全」醫美診所被爆涉嫌惡性倒閉，積欠多家廠商欠款，貴婦奈奈和黃博健兩人則去向不明，被許多網友和債主上網留言兩人跑路了。貴婦奈奈2日晚間則在臉書發文，除向各界道歉外，也強調她和先生黃博健並未捲款，黃博健直到最後一刻還在籌錢過票，但仍不敵某些人的高利滾利、重利侵占。警方3日表示，已接獲一名民眾報案提告貴婦奈奈夫妻詐欺，目前已掌握兩人行蹤。警方昨天下午向台北地檢署報請指揮偵辦，北檢已指派專案檢察官偵辦；不過，就在檢警對這對夫妻發布境管通報前，他們就已搭機飛往舊金山，若日後拒不到案，檢方不排除發布通緝。': '社會'}]

In [2778]:
def get_featuresets(books=books,top=200):
    title_featuresets = []
    txt_featuresets = []
    for book in books:

        title_featureset = get_title_featuresets(book,top)
        title_featuresets.append(title_featureset)
        
        txt_featureset = get_txt_featuresets(book,top)
        txt_featuresets.append(txt_featureset)
    return title_featuresets, txt_featuresets

In [ ]:
title_featuresets, txt_featuresets = get_featuresets(top=300)

貴婦1社會
奈奈1社會
黃博1社會
健1社會
護照1社會
杏1社會
立博1社會
詐欺1社會
檢警1社會
搭機1社會
地檢署1社會
持1社會
夫妻1社會
偵辦1社會
獲報1社會
報案1社會
提告1社會
報請1社會
指揮1社會
北檢1社會
專案1社會
到案1社會
通緝1社會
不敵1運動
預警1兩岸
留言1娛樂
道歉1娛樂
貴婦,社會
奈奈,社會
黃博,社會
健,社會
護照,社會
杏,社會
立博,社會
詐欺,社會
檢警,社會
搭機,社會
地檢署,社會
持,社會
夫妻,社會
偵辦,社會
獲報,社會
報案,社會
提告,社會
報請,社會
指揮,社會
北檢,社會
專案,社會
到案,社會
通緝,社會
中華民國護照1科技
先生黃博1科技
杏立博1科技
立博全1科技
全醫美1科技
醫美診所1科技
網紅貴婦1科技
健合開1科技
無預警1科技
預警歇業1科技
涉詐欺1科技
多家廠商1科技
已接獲1科技
民眾報案1科技
奈奈夫妻1科技
已掌握1科技
警方昨天1科技
昨天下午1科技
指揮偵辦1科技
檢察官偵辦1科技
發布通緝1科技
中華民國護照1地方
先生黃博1地方
杏立博1地方
立博全1地方
全醫美1地方
醫美診所1地方
網紅貴婦1地方
健合開1地方
無預警1地方
預警歇業1地方
涉詐欺1地方
多家廠商1地方
已接獲1地方
民眾報案1地方
奈奈夫妻1地方
已掌握1地方
警方昨天1地方
昨天下午1地方
指揮偵辦1地方
檢察官偵辦1地方
發布通緝1地方
中華民國護照1社會
先生黃博1社會
杏立博1社會
立博全1社會
全醫美1社會
醫美診所1社會
網紅貴婦1社會
健合開1社會
無預警1社會
預警歇業1社會
涉詐欺1社會
多家廠商1社會
已接獲1社會
民眾報案1社會
奈奈夫妻1社會
已掌握1社會
警方昨天1社會
昨天下午1社會
指揮偵辦1社會
檢察官偵辦1社會
發布通緝1社會
中華民國護照1運動
先生黃博1運動
杏立博1運動
立博全1運動
全醫美1運動
醫美診所1運動
網紅貴婦1運動
健合開1運動
無預警1運動
預警歇業1運動
涉詐欺1運動
多家廠商1運動
已接獲1運動
民眾報案1運動
奈奈夫妻1運動
已掌握1運動
警方昨天1運動
昨天下午1運動
指揮偵辦1運動
檢察官偵辦1運動
發布通緝1運動
中華民國護照1兩岸
先生黃博1兩岸
杏立博1兩岸
立博全1兩岸
全醫美1兩岸
醫美診所1兩岸
網紅貴婦1

實驗室1科技
表面1科技
對抗1科技
業界1科技
科學家1科技
新創1科技
中斷1科技
速度1科技
理解1地方
鎖定1社會
戰1運動
戰局1運動
逆轉1運動
回到1運動
陷入1兩岸
收購1證券
大幅1證券
獎勵1生活
跨國1娛樂
嘗試1娛樂
之外1娛樂
崔大偉1國際
冷戰1國際
外國1國際
竊取1國際
戰略1國際
WTO1國際
糾正1政治
勢力1政治
經歷1文化
學術1文化
實驗室,科技
表面,科技
對抗,科技
業界,科技
科學家,科技
新創,科技
中斷,科技
速度,科技
科技企業1科技
科技企業1地方
科技企業1社會
科技企業1運動
科技企業1兩岸
科技企業1證券
科技企業1生活
科技企業1娛樂
科技企業1國際
科技企業1產經
科技企業1政治
科技企業1文化
一步1科技
有助1科技
晚上1地方
幫忙1運動
輸1運動
慢慢1運動
司機1兩岸
症狀1生活
注意1生活
白天1生活
九合一1政治
最好1政治
大選1政治
幫忙,運動
輸,運動
慢慢,運動
收到1科技
受傷1社會
打拚1運動
大聯盟1運動
投手1運動
球季1運動
打球1運動
球場1運動
放棄1運動
習慣1運動
重返1運動
球隊1運動
沒辦法1運動
回到1運動
投手丘1運動
投1運動
中信1運動
棒球1運動
球速1運動
開季1運動
勝1運動
敗1運動
防禦率1運動
兄弟1證券
執導1娛樂
上映1娛樂
現身1娛樂
講述1娛樂
證明1產經
國民1政治
當初1文化
記錄1文化
打拚,運動
大聯盟,運動
投手,運動
球季,運動
打球,運動
球場,運動
放棄,運動
習慣,運動
重返,運動
球隊,運動
沒辦法,運動
回到,運動
投手丘,運動
投,運動
中信,運動
棒球,運動
球速,運動
開季,運動
勝,運動
敗,運動
防禦率,運動
陳惟揚1科技
美國打拚1科技
球季結束1科技
中信兄弟1科技
棒球學校1科技
繳出勝1科技
勝敗1科技
陳惟揚1地方
美國打拚1地方
球季結束1地方
中信兄弟1地方
棒球學校1地方
繳出勝1地方
勝敗1地方
陳惟揚1社會
美國打拚1社會
球季結束1社會
中信兄弟1社會
棒球學校1社會
繳出勝1社會
勝敗1社會
陳惟揚1運動
美國打拚1運動
球季結束1運動
中信兄弟1運動
棒球學校1運動
繳出勝1運動
勝敗1運動
陳惟揚1兩岸
美國打拚1兩岸
球季結束1兩岸
中信兄弟1兩岸
棒球學校1兩岸
繳出勝

台幣1娛樂
散文1文化
金典獎1文化
文學1文化
小說1文化
文學獎1文化
客語1文化
原住民1文化
台文館1文化
得主1文化
讀者1文化
閱讀1文化
評選1文化
馮翊綱1文化
津1文化
文字1文化
散文,文化
金典獎,文化
文學,文化
小說,文化
文學獎,文化
客語,文化
原住民,文化
台文館,文化
得主,文化
讀者,文化
閱讀,文化
評選,文化
馮翊綱,文化
津,文化
文字,文化
台灣文學1科技
長篇小說1科技
台語散文1科技
客語散文1科技
原住民漢語1科技
漢語散文1科技
得獎名單1科技
劇本台語1科技
散文客語1科技
件作品1科技
小說散文1科技
台灣文學1地方
長篇小說1地方
台語散文1地方
客語散文1地方
原住民漢語1地方
漢語散文1地方
得獎名單1地方
劇本台語1地方
散文客語1地方
件作品1地方
小說散文1地方
台灣文學1社會
長篇小說1社會
台語散文1社會
客語散文1社會
原住民漢語1社會
漢語散文1社會
得獎名單1社會
劇本台語1社會
散文客語1社會
件作品1社會
小說散文1社會
台灣文學1運動
長篇小說1運動
台語散文1運動
客語散文1運動
原住民漢語1運動
漢語散文1運動
得獎名單1運動
劇本台語1運動
散文客語1運動
件作品1運動
小說散文1運動
台灣文學1兩岸
長篇小說1兩岸
台語散文1兩岸
客語散文1兩岸
原住民漢語1兩岸
漢語散文1兩岸
得獎名單1兩岸
劇本台語1兩岸
散文客語1兩岸
件作品1兩岸
小說散文1兩岸
台灣文學1證券
長篇小說1證券
台語散文1證券
客語散文1證券
原住民漢語1證券
漢語散文1證券
得獎名單1證券
劇本台語1證券
散文客語1證券
件作品1證券
小說散文1證券
台灣文學1生活
長篇小說1生活
台語散文1生活
客語散文1生活
原住民漢語1生活
漢語散文1生活
得獎名單1生活
劇本台語1生活
散文客語1生活
件作品1生活
小說散文1生活
台灣文學1娛樂
長篇小說1娛樂
台語散文1娛樂
客語散文1娛樂
原住民漢語1娛樂
漢語散文1娛樂
得獎名單1娛樂
劇本台語1娛樂
散文客語1娛樂
件作品1娛樂
小說散文1娛樂
台灣文學1國際
長篇小說1國際
台語散文1國際
客語散文1國際
原住民漢語1國際
漢語散文1國際
得獎名單1國際
劇本台語1國際
散文客語1國際
件作品1國際
小說散文1國際
台灣文學1產經
長篇小說1產

高速1科技
商用1兩岸
商轉1證券
投顧1證券
光通訊1證券
市占率1證券
傳輸1證券
貢獻度1證券
規格1證券
基地台1證券
高階1證券
網通1證券
處理器1證券
功率1證券
華星光1證券
終端1證券
T1國際
競爭力1產經
時程1政治
處罰1政治
商轉,證券
投顧,證券
光通訊,證券
市占率,證券
傳輸,證券
貢獻度,證券
規格,證券
基地台,證券
高階,證券
網通,證券
處理器,證券
功率,證券
華星光,證券
終端,證券
設備全球1科技
市場擔心1科技
目前全球1科技
市占率約1科技
超過成1科技
占營收1科技
營收比重1科技
設備全球1地方
市場擔心1地方
目前全球1地方
市占率約1地方
超過成1地方
占營收1地方
營收比重1地方
設備全球1社會
市場擔心1社會
目前全球1社會
市占率約1社會
超過成1社會
占營收1社會
營收比重1社會
設備全球1運動
市場擔心1運動
目前全球1運動
市占率約1運動
超過成1運動
占營收1運動
營收比重1運動
設備全球1兩岸
市場擔心1兩岸
目前全球1兩岸
市占率約1兩岸
超過成1兩岸
占營收1兩岸
營收比重1兩岸
設備全球1證券
市場擔心1證券
目前全球1證券
市占率約1證券
超過成1證券
占營收1證券
營收比重1證券
設備全球1生活
市場擔心1生活
目前全球1生活
市占率約1生活
超過成1生活
占營收1生活
營收比重1生活
設備全球1娛樂
市場擔心1娛樂
目前全球1娛樂
市占率約1娛樂
超過成1娛樂
占營收1娛樂
營收比重1娛樂
設備全球1國際
市場擔心1國際
目前全球1國際
市占率約1國際
超過成1國際
占營收1國際
營收比重1國際
設備全球1產經
市場擔心1產經
目前全球1產經
市占率約1產經
超過成1產經
占營收1產經
營收比重1產經
設備全球1政治
市場擔心1政治
目前全球1政治
市占率約1政治
超過成1政治
占營收1政治
營收比重1政治
設備全球1文化
市場擔心1文化
目前全球1文化
市占率約1文化
超過成1文化
占營收1文化
營收比重1文化
產學1科技
學研1科技
三方1科技
專利1科技
行銷1地方
加盟1運動
西班牙1運動
微博1兩岸
商務1兩岸
麗豐1證券
佐登1證券
年增1證券
克麗緹娜1證券
通路1證券
月增1證券
連鎖1證券
上市1證券
擴張1證券
效應1證券
單月1證券
年增率1證券
正成長1證券

一步1科技
充電1科技
新創1科技
路線1地方
突然1社會
全場1運動
一天1證券
春節1證券
老師1生活
伍思凱1娛樂
演唱1娛樂
演唱會1娛樂
歌手1娛樂
歌迷1娛樂
綜藝1娛樂
唱片1娛樂
辦1娛樂
演藝1娛樂
變成1娛樂
音樂人1娛樂
獻唱1娛樂
金曲1娛樂
校園1產經
還要1政治
連署1政治
鋼琴1文化
伍思凱,娛樂
演唱,娛樂
演唱會,娛樂
歌手,娛樂
歌迷,娛樂
綜藝,娛樂
唱片,娛樂
辦,娛樂
演藝,娛樂
變成,娛樂
音樂人,娛樂
獻唱,娛樂
金曲,娛樂
綜藝節目1科技
人生故事1科技
綜藝節目1地方
人生故事1地方
綜藝節目1社會
人生故事1社會
綜藝節目1運動
人生故事1運動
綜藝節目1兩岸
人生故事1兩岸
綜藝節目1證券
人生故事1證券
綜藝節目1生活
人生故事1生活
綜藝節目1娛樂
人生故事1娛樂
綜藝節目1國際
人生故事1國際
綜藝節目1產經
人生故事1產經
綜藝節目1政治
人生故事1政治
綜藝節目1文化
人生故事1文化
數據機1科技
搭載1科技
聯發科1證券
曦力1證券
傳輸1證券
支援1證券
移動1生活
製造商1國際
聯發科,證券
曦力,證券
傳輸,證券
支援,證券
相關產品1科技
相關產品1地方
相關產品1社會
相關產品1運動
相關產品1兩岸
相關產品1證券
相關產品1生活
相關產品1娛樂
相關產品1國際
相關產品1產經
相關產品1政治
相關產品1文化
研究員1科技
裝置1科技
有意1地方
交手1運動
輸1運動
B1兩岸
致1證券
本週1證券
久1娛樂
多年1娛樂
華府1國際
間諜1國際
任正1國際
竊取1國際
參議員1國際
舟是1國際
解放軍1國際
大使1國際
強烈1國際
民主黨1國際
軍方1國際
巨擘1國際
干預1國際
T1國際
國人1政治
失利1政治
華府,國際
間諜,國際
任正,國際
竊取,國際
參議員,國際
舟是,國際
解放軍,國際
大使,國際
強烈,國際
民主黨,國際
軍方,國際
巨擘,國際
干預,國際
T,國際
網路間諜1科技
間諜活動1科技
費德勒1科技
雙邊關係1科技
孟晚舟是1科技
舟是華為1科技
創辦人任正1科技
非曾1科技
華為違反1科技
美國已1科技
已提出1科技
提出引渡1科技
美國科技1科技
長期以來1科技
以來美國1科技
美國官員1科技
國會議員1科技
顯示華為1科技
中國公司1科技
使用華為1科技
通

...

即日起至1地方
茱莉亞學院1社會
大學預科1社會
預科課程1社會
已開放1社會
開放申請1社會
即日起至1社會
茱莉亞學院1運動
大學預科1運動
預科課程1運動
已開放1運動
開放申請1運動
即日起至1運動
茱莉亞學院1兩岸
大學預科1兩岸
預科課程1兩岸
已開放1兩岸
開放申請1兩岸
即日起至1兩岸
茱莉亞學院1證券
大學預科1證券
預科課程1證券
已開放1證券
開放申請1證券
即日起至1證券
茱莉亞學院1生活
大學預科1生活
預科課程1生活
已開放1生活
開放申請1生活
即日起至1生活
茱莉亞學院1娛樂
大學預科1娛樂
預科課程1娛樂
已開放1娛樂
開放申請1娛樂
即日起至1娛樂
茱莉亞學院1國際
大學預科1國際
預科課程1國際
已開放1國際
開放申請1國際
即日起至1國際
茱莉亞學院1產經
大學預科1產經
預科課程1產經
已開放1產經
開放申請1產經
即日起至1產經
茱莉亞學院1政治
大學預科1政治
預科課程1政治
已開放1政治
開放申請1政治
即日起至1政治
茱莉亞學院1文化
大學預科1文化
預科課程1文化
已開放1文化
開放申請1文化
即日起至1文化
日圓1運動
自結1證券
歷年1證券
子公司1證券
結合併1證券
大增1證券
趨緩1證券
穩健1證券
淡季1證券
保守1證券
股1證券
純益1證券
獲利1證券
台幣1娛樂
自結,證券
歷年,證券
子公司,證券
結合併,證券
大增,證券
趨緩,證券
穩健,證券
淡季,證券
保守,證券
股,證券
純益,證券
獲利,證券
同期億1科技
營運表現1科技
歷年同期1科技
同期新高1科技
元減少1科技
元增加1科技
增加累計1科技
結合併營收1科技
元大增1科技
影響中國1科技
法人預估1科技
股純益1科技
創歷年1科技
先前預估1科技
同期億1地方
營運表現1地方
歷年同期1地方
同期新高1地方
元減少1地方
元增加1地方
增加累計1地方
結合併營收1地方
元大增1地方
影響中國1地方
法人預估1地方
股純益1地方
創歷年1地方
先前預估1地方
同期億1社會
營運表現1社會
歷年同期1社會
同期新高1社會
元減少1社會
元增加1社會
增加累計1社會
結合併營收1社會
元大增1社會
影響中國1社會
法人預估1社會
股純益1社會
創歷年1社會
先前預估1社會
同期億1運動
營運表現1運動
歷年同期1運動
同期新高1運動
元減

物質1科技
水土1地方
核能1地方
市政1地方
理解1地方
戶外1地方
尤其1運動
保守1證券
核准1生活
周邊1生活
建置1生活
核定1生活
微型1生活
發言1娛樂
核一1產經
乾貯1產經
乾貯場1產經
證明1產經
貯存場1產經
乾式1產經
圖1產經
執照1產經
室外1產經
室內1產經
夠1政治
不足1政治
歷經1文化
結晶1文化
核一,產經
乾貯,產經
乾貯場,產經
證明,產經
貯存場,產經
乾式,產經
圖,產經
執照,產經
室外,產經
室內,產經
未達1科技
完工證明1科技
除役工作1科技
保持完工1科技
核一乾貯1科技
核一廠乾貯1科技
室內乾貯1科技
未達1地方
完工證明1地方
除役工作1地方
保持完工1地方
核一乾貯1地方
核一廠乾貯1地方
室內乾貯1地方
未達1社會
完工證明1社會
除役工作1社會
保持完工1社會
核一乾貯1社會
核一廠乾貯1社會
室內乾貯1社會
未達1運動
完工證明1運動
除役工作1運動
保持完工1運動
核一乾貯1運動
核一廠乾貯1運動
室內乾貯1運動
未達1兩岸
完工證明1兩岸
除役工作1兩岸
保持完工1兩岸
核一乾貯1兩岸
核一廠乾貯1兩岸
室內乾貯1兩岸
未達1證券
完工證明1證券
除役工作1證券
保持完工1證券
核一乾貯1證券
核一廠乾貯1證券
室內乾貯1證券
未達1生活
完工證明1生活
除役工作1生活
保持完工1生活
核一乾貯1生活
核一廠乾貯1生活
室內乾貯1生活
未達1娛樂
完工證明1娛樂
除役工作1娛樂
保持完工1娛樂
核一乾貯1娛樂
核一廠乾貯1娛樂
室內乾貯1娛樂
未達1國際
完工證明1國際
除役工作1國際
保持完工1國際
核一乾貯1國際
核一廠乾貯1國際
室內乾貯1國際
未達1產經
完工證明1產經
除役工作1產經
保持完工1產經
核一乾貯1產經
核一廠乾貯1產經
室內乾貯1產經
未達1政治
完工證明1政治
除役工作1政治
保持完工1政治
核一乾貯1政治
核一廠乾貯1政治
室內乾貯1政治
未達1文化
完工證明1文化
除役工作1文化
保持完工1文化
核一乾貯1文化
核一廠乾貯1文化
室內乾貯1文化
賣壓1證券
重挫1證券
道瓊1證券
普爾1證券
科技股1證券
那斯1證券
達克1證券
指數跌1證券
賣壓,證券
重挫,證券
道瓊,證券
普爾,證券
科技股,證券
那斯,證券
達克,證券
指數跌,證券
被捕令1科技
令市場1

打點安打1社會
敲出二壘1社會
打點局1社會
午場賽事1社會
韓職聯隊1社會
日本社會1運動
森下翔平1運動
分打點1運動
二壘安打1運動
三壘安打1運動
帶有分1運動
阿部翔太1運動
辻野雄大1運動
安打帶有1運動
敲出打點1運動
敲出支1運動
支安打1運動
冬季聯盟1運動
局失分1運動
支長打1運動
拿下連勝1運動
連續安打1運動
攻下分1運動
分之後1運動
佐藤龍彥1運動
敲二壘1運動
分皆1運動
攻分1運動
分局上1運動
拿下勝利1運動
單場MVP1運動
先發投手1運動
主投局1運動
安打失掉1運動
失掉分1運動
優質先發1運動
敲安打1運動
安打包辦1運動
包辦分1運動
場比賽1運動
分局下1運動
打點安打1運動
敲出二壘1運動
打點局1運動
午場賽事1運動
韓職聯隊1運動
日本社會1兩岸
森下翔平1兩岸
分打點1兩岸
二壘安打1兩岸
三壘安打1兩岸
帶有分1兩岸
阿部翔太1兩岸
辻野雄大1兩岸
安打帶有1兩岸
敲出打點1兩岸
敲出支1兩岸
支安打1兩岸
冬季聯盟1兩岸
局失分1兩岸
支長打1兩岸
拿下連勝1兩岸
連續安打1兩岸
攻下分1兩岸
分之後1兩岸
佐藤龍彥1兩岸
敲二壘1兩岸
分皆1兩岸
攻分1兩岸
分局上1兩岸
拿下勝利1兩岸
單場MVP1兩岸
先發投手1兩岸
主投局1兩岸
安打失掉1兩岸
失掉分1兩岸
優質先發1兩岸
敲安打1兩岸
安打包辦1兩岸
包辦分1兩岸
場比賽1兩岸
分局下1兩岸
打點安打1兩岸
敲出二壘1兩岸
打點局1兩岸
午場賽事1兩岸
韓職聯隊1兩岸
日本社會1證券
森下翔平1證券
分打點1證券
二壘安打1證券
三壘安打1證券
帶有分1證券
阿部翔太1證券
辻野雄大1證券
安打帶有1證券
敲出打點1證券
敲出支1證券
支安打1證券
冬季聯盟1證券
局失分1證券
支長打1證券
拿下連勝1證券
連續安打1證券
攻下分1證券
分之後1證券
佐藤龍彥1證券
敲二壘1證券
分皆1證券
攻分1證券
分局上1證券
拿下勝利1證券
單場MVP1證券
先發投手1證券
主投局1證券
安打失掉1證券
失掉分1證券
優質先發1證券
敲安打1證券
安打包辦1證券
包辦分1證券
場比賽1證券
分局下1證券
打點安打1證券
敲出二壘1證券
打點局1證券
午場賽事1證券
韓職聯隊1證券
日本社會1生活
森下翔平1生活
分打點1生活
二壘安打1生活
三壘安打1生

流程1科技
主題館1科技
ID1科技
用戶1科技
帳號1科技
介面1科技
隱私1科技
證書1地方
合約1運動
FIDO1證券
特徵1證券
支援1證券
雲端1生活
科技展1產經
金管會1產經
事項1政治
藉由1文化
流程,科技
主題館,科技
ID,科技
用戶,科技
帳號,科技
介面,科技
隱私,科技
Dialog1科技
外媒1科技
大廠1科技
充電1科技
版1科技
平常1運動
解讀1兩岸
市況1證券
VCSEL1證券
終端1證券
拉貨1證券
力道1證券
趨緩1證券
銷量1產經
面板1產經
市況,證券
VCSEL,證券
終端,證券
拉貨,證券
力道,證券
趨緩,證券
客戶需求1科技
超過成1科技
比重約1科技
客戶需求1地方
超過成1地方
比重約1地方
客戶需求1社會
超過成1社會
比重約1社會
客戶需求1運動
超過成1運動
比重約1運動
客戶需求1兩岸
超過成1兩岸
比重約1兩岸
客戶需求1證券
超過成1證券
比重約1證券
客戶需求1生活
超過成1生活
比重約1生活
客戶需求1娛樂
超過成1娛樂
比重約1娛樂
客戶需求1國際
超過成1國際
比重約1國際
客戶需求1產經
超過成1產經
比重約1產經
客戶需求1政治
超過成1政治
比重約1政治
客戶需求1文化
超過成1文化
比重約1文化
Instagram1科技
帳號1科技
名為1科技
結婚1社會
月前1社會
老婆1運動
賈斯汀1娛樂
歌手1娛樂
人氣1娛樂
天后1娛樂
執照1產經
模特兒1文化
出生1文化
賈斯汀,娛樂
歌手,娛樂
人氣,娛樂
天后,娛樂
美國演員1科技
兼演員1科技
美國演員1地方
兼演員1地方
美國演員1社會
兼演員1社會
美國演員1運動
兼演員1運動
美國演員1兩岸
兼演員1兩岸
美國演員1證券
兼演員1證券
美國演員1生活
兼演員1生活
美國演員1娛樂
兼演員1娛樂
美國演員1國際
兼演員1國際
美國演員1產經
兼演員1產經
美國演員1政治
兼演員1政治
美國演員1文化
兼演員1文化
藍綠1地方
直轄市1地方
勝利1運動
輸1運動
多數1生活
姚文智1政治
選區1政治
迴廊1政治
反省1政治
民意1政治
執政1政治
留下1文化
角度1文化
姚文智,政治
選區,政治
迴廊,政治
反省,政治
民意,政治
執政,政治
下一局挑戰1科技
相關議題1科技
引發關注1科技
選區立委1科技
總統府進行1科技
進

人類,科技
科學家,科技
地球,科技
太空,科技
總署,科技
NASA,科技
旅行,科技
一步,科技
方法,科技
柯倫巴1科技
倫巴諾1科技
超高智慧1科技
外星生命1科技
國家航空1科技
航空暨1科技
暨太空1科技
太空總署1科技
總署NASA1科技
英國每日1科技
科學方法1科技
柯倫巴1地方
倫巴諾1地方
超高智慧1地方
外星生命1地方
國家航空1地方
航空暨1地方
暨太空1地方
太空總署1地方
總署NASA1地方
英國每日1地方
科學方法1地方
柯倫巴1社會
倫巴諾1社會
超高智慧1社會
外星生命1社會
國家航空1社會
航空暨1社會
暨太空1社會
太空總署1社會
總署NASA1社會
英國每日1社會
科學方法1社會
柯倫巴1運動
倫巴諾1運動
超高智慧1運動
外星生命1運動
國家航空1運動
航空暨1運動
暨太空1運動
太空總署1運動
總署NASA1運動
英國每日1運動
科學方法1運動
柯倫巴1兩岸
倫巴諾1兩岸
超高智慧1兩岸
外星生命1兩岸
國家航空1兩岸
航空暨1兩岸
暨太空1兩岸
太空總署1兩岸
總署NASA1兩岸
英國每日1兩岸
科學方法1兩岸
柯倫巴1證券
倫巴諾1證券
超高智慧1證券
外星生命1證券
國家航空1證券
航空暨1證券
暨太空1證券
太空總署1證券
總署NASA1證券
英國每日1證券
科學方法1證券
柯倫巴1生活
倫巴諾1生活
超高智慧1生活
外星生命1生活
國家航空1生活
航空暨1生活
暨太空1生活
太空總署1生活
總署NASA1生活
英國每日1生活
科學方法1生活
柯倫巴1娛樂
倫巴諾1娛樂
超高智慧1娛樂
外星生命1娛樂
國家航空1娛樂
航空暨1娛樂
暨太空1娛樂
太空總署1娛樂
總署NASA1娛樂
英國每日1娛樂
科學方法1娛樂
柯倫巴1國際
倫巴諾1國際
超高智慧1國際
外星生命1國際
國家航空1國際
航空暨1國際
暨太空1國際
太空總署1國際
總署NASA1國際
英國每日1國際
科學方法1國際
柯倫巴1產經
倫巴諾1產經
超高智慧1產經
外星生命1產經
國家航空1產經
航空暨1產經
暨太空1產經
太空總署1產經
總署NASA1產經
英國每日1產經
科學方法1產經
柯倫巴1政治
倫巴諾1政治
超高智慧1政治
外星生命1政治
國家航空1政治
航空暨1政治
暨太空1政治
太空總署1政治
總署NASA1政治
英國每日1政治
科學方法1

In [ ]:
#txt_featuresets
'研究院' in [w for li in txt_fwords.values() for w in li]
books[0]

In [ ]:
title_featuresets

In [ ]:
title_featuresets = title_featuresets.copy()
size = int(len(title_featuresets)*0.7)
train_set, test_set = title_featuresets[:size], title_featuresets[size:]
title_classifier = nltk.NaiveBayesClassifier.train(train_set)
nltk.classify.accuracy(classifier, test_set)

In [ ]:
txt_featuresets = txt_featuresets.copy()
size = int(len(txt_featuresets)*0.7)
train_set, test_set = txt_featuresets[:size], txt_featuresets[size:]
txt_classifier = nltk.NaiveBayesClassifier.train(train_set)
nltk.classify.accuracy(classifier, test_set)

In [ ]:
title_comanswer = classifier.classify_many([i[0] for i in title_featuresets])
txt_comanswer = classifier.classify_many([i[0] for i in txt_featuresets])

In [ ]:
title_answer = [i[1] for i in title_featuresets]
txt_answer = [i[1] for i in txt_featuresets]

In [ ]:
txt_top = [list(get_top(txt,200).values())[0] for txt in [list(book[1].keys())[0] for book in books]]
txt_top

In [ ]:
import pandas as pd
import numpy as np

In [ ]:
title_correct = ['F' if w != title_answer[title_comanswer.index(w)] else 'T' for w in title_comanswer ]
txt_correct = ['F' if w != txt_answer[txt_comanswer.index(w)] else 'T' for w in txt_comanswer ]

In [ ]:
df = pd.DataFrame([txt_comanswer,txt_answer,txt_top,txt_correct,title_comanswer,title_answer,title_correct],index=['txt_comanswer','txt_answer','txt_top','txt_correct','title_comanswer','title_answer','title_correct']).T

In [ ]:
df.loc[df['title_correct']=='T',:]
df.head(10)

In [ ]:
txt_featuresets

In [ ]:
dataset = []
#answer_dict={}
answer = ""
for i,v in df.iterrows():
#    print(v)
    answer_dict={}
    print(v)
    answer_dict['txt_comanswer']=v[0]
    answer_dict['txt_top']=v[2]
    answer_dict['title_comanswer']=v[4]

    answer = v[1]
    dataset.append((answer_dict,answer))

In [ ]:
dataset[:]

In [ ]:
df

In [ ]:
#len([i for i in get_featuresets(top = 5)[0][size:] if i[0]=={}])

In [ ]:
size = int(len(dataset)*0.7)
train_data, test_data = dataset[:size], dataset[size:]

In [ ]:
test_data2 = [i[0] for i in test_data]

In [ ]:
from nltk.classify import SklearnClassifier
from sklearn.naive_bayes import BernoulliNB
from sklearn.svm import SVC

In [ ]:
classif = SklearnClassifier(BernoulliNB()).train(train_data)

In [ ]:
classif.classify_many(test_data2)
classif = SklearnClassifier(SVC(), sparse=False).train(train_data)
classif.classify_many(test_data2)

In [ ]:
ch = []
n=0
for f in dataset[size:] :
    ch.append([f,classif.classify_many(test_data2)[n]])
    n += 1


ch

In [ ]:
back = classif.classify_many(test_data2)
[i[1] for i in test_data]

In [ ]:
n = 0
p=0
while n < len(back):
    if back[n] ==  [i[1] for i in test_data][n]:
 #       print([back[n], [i[1] for i in test_data][n]])
        p += 1
    n += 1
print(p)
print(p/len(back))
    

In [ ]:
test_news="""
資深媒體人劉寶傑確定向主持11年的《關鍵時刻》請辭，將在明年1月永久交出主持棒，他超生動的主持方式，樹立獨特個人風格，深獲不少觀眾喜愛，因此告別《關鍵》後的下一步一直備受矚目，有消息傳出，劉寶傑之後將轉戰年代，取代跟《關鍵》同時段的《新聞追追追》。

檢視相片
▲劉寶傑下一步動向備受矚目。（圖／翻攝自臉書）

年代《新聞追追追》由主播安幼琪與張啟楷搭檔主持7年，不過《自由時報》報導，劉寶傑可能到年代，《追追追》恐怕面臨收攤危機，但年代內部知情人士指出，電視台的老闆政治立場和劉寶傑不同，挖角的機率應該不大，認為節目不會收攤，但可能會轉型或改節目名稱，主持人或許也會有變動。

檢視相片
▲《新聞追追追》恐收攤？（圖／翻攝自YouTube）

對此，安幼琪透露上周公司內部確實有開會，但只是針對節目來賓的選擇做小調整，希望能夠多聽年輕人的聲音，也表示跟搭檔張啟楷合作得很愉快，而張啟楷則回應沒有聽過類似的消息。

"""
f = pos_txt_features(test_news,100)
t =  pos_title_features(test_news,300)

print(classifier.classify(f))
print(classifier.classify(t))
print(f)

In [ ]:
def get_lab(title='',txt='',top=200):
    f = pos_txt_features(txt,top)
    t =  pos_title_features(title,top)
    top = list(get_top(txt,top).values())[0]
    print(top)
#    t = get_title_featuresets([txt,top])
#    f = get_txt_featuresets([title,top])
    if len(t.keys()) < 2:
        final = classif.classify_many({'txt_comanswer': classifier.classify(f),'txt_top':top})
        final_title = ""
    elif classifier.classify(t) == classifier.classify(f) and classifier.classify(f)==top and top == classifier.classify(t):
        final = classifier.classify(f)
        final_title = classifier.classify(t)
    else:
        final = classif.classify_many({'title_comanswer': classifier.classify(t), 'txt_comanswer': classifier.classify(f),'txt_top':top})
        final_title = classifier.classify(t)
    print(f)
    print([final_title,classifier.classify(f)])
#    print(classifier.classify(t))
    return final

In [ ]:
test_title="""
籲國人別再出言刺激日本 謝長廷挨轟「助」日代表


"""

In [ ]:
test_txt="""
日本外相河野太郎 7 日指出，台灣日前公投通過反對日本核災 5 縣食品進口一事，可能影響到台灣能否加入跨太平洋夥伴全面進步協定（CPTPP）。對此，我駐日代表謝長廷表示，將持續與日方溝通，也希望少數國人不要再出言刺激日本。此話一出，讓網友群起嘲諷，怒轟他根本是「助日代表」。



河野太郎 7 日對台灣公投通過反日本核災 5 縣食品進口一事表態，認為食品管制要有科學根據，且台灣此舉可能違反 WTO 規則，日方不排除向 WTO 申訴，而台灣想加入 CPTPP ，但可能會因為此事而受到影響，他感到相當遺憾。



檢視相片
▲日本外相河野太郎表示，台灣想加入跨太平洋夥伴全面進步協定（CPTPP）「可能因為這樣的事態而變得無法參加，非常遺憾」。（圖／翻攝自河野太郎twitter）



據《中央社》報導，駐日代表謝長廷 7 日晚間在東京出席活動，受訪時對此表示，將持續與日本積極溝通、說明，畢竟台灣是民主社會，對公投結果基本上要尊重，希望不會因此影響到台灣跟日本的友好關係，並向國人喊話，希望少數民眾不要再出言刺激日本，一直說「日本不敢啦」、「日本如果怎麼樣，日本自己吃虧」這類的話，這樣的刺激性言論沒有意義。



被問到可否預想到日本會採取什麼報復措施時，謝長廷表示不敢預測，希望國內不要再刺激日方，且日本內部也有不同意見，有人認為不對此事做出反應，若其他國家也用民粹表決，可能會影響到自由貿易；也有人認為這是台灣的民主制度，可以體諒。



至於有人認為南韓不理日本，「南韓能，台灣為何不能？」謝長廷則說，南韓無求於日本，但台灣有很多事需要拜託日本幫忙，像爭取加入 CPTPP 、希望日本在 WHO 等國際組織上幫台灣發聲等，如果退到跟南韓一樣，對台灣會是一大損失。謝長廷指出，台灣對於日本食品的管制還是比中國大陸寬鬆，但中國大陸、香港都在放寬，但台灣卻在緊縮，日本人的感受很不一樣。



謝長廷這番言論在 PTT 引發熱議，鄉民們紛紛留言砲轟「助日代表」、「出言刺激日本？噁心耶，你領哪一國薪水啊」、「日本政府過去從來沒有在國際場合幫台灣講話過，從來沒有」、「臺日友好是講民間，日本政府過去怎麼欺負臺灣」、「打一開始就沒要讓我們參加不是嗎，每年貿易逆差有多少知道嗎？次級品不良品改標賣來台灣，有負責過嗎？想想大創、阻尼器，國際沒有友誼，只有利益」、「政府怪網友刺激外國？這...」。
"""

In [ ]:
get_lab(title=test_title,txt=test_txt,top=200)

In [ ]:
pos_title_features(test_title,300)

In [ ]:
for i in list(pos_txt_features(test_txt,300).keys()):
    print([i,i in txt_fwords['娛樂']])

In [ ]:
txt_fwords['娛樂']

In [ ]:
ujujuj ={}
len(ujujuj.keys()) < 2